In [25]:
#Importing the necessary libraries
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel,cosine_similarity
import tensorflow as tf

In [2]:
#Loading the dataset
data = pd.read_csv("D:\\SLIIT\\3rd year 2nd sem\\Information Retrieval and Web Analytics\\Coding\\ratings_Beauty.csv")
data.head(10)

UserId   ProductId  Rating   Timestamp
0  A39HTATAQ9V7YF  0205616461     5.0  1369699200
1  A3JM6GV9MNOF9X  0558925278     3.0  1355443200
2  A1Z513UWSAAO0F  0558925278     5.0  1404691200
3  A1WMRR494NWEWV  0733001998     4.0  1382572800
4  A3IAAVS479H7M7  0737104473     1.0  1274227200
5   AKJHHD5VEH7VG  0762451459     5.0  1404518400
6  A1BG8QW55XHN6U  1304139212     5.0  1371945600
7  A22VW0P4VZHDE3  1304139220     5.0  1373068800
8  A3V3RE4132GKRO  130414089X     5.0  1401840000
9  A327B0I7CYTEJC  130414643X     4.0  1389052800

In [3]:
#Exploring the dataset
data.describe()

Rating     Timestamp
count  2.023070e+06  2.023070e+06
mean   4.149036e+00  1.360389e+09
std    1.311505e+00  4.611860e+07
min    1.000000e+00  9.087552e+08
25%    4.000000e+00  1.350259e+09
50%    5.000000e+00  1.372810e+09
75%    5.000000e+00  1.391472e+09
max    5.000000e+00  1.406074e+09

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2023070 entries, 0 to 2023069
Data columns (total 4 columns):
 #   Column     Dtype  
---  ------     -----  
 0   UserId     object 
 1   ProductId  object 
 2   Rating     float64
 3   Timestamp  int64  
dtypes: float64(1), int64(1), object(2)
memory usage: 61.7+ MB


In [5]:
data.isna().sum()

UserId       0
ProductId    0
Rating       0
Timestamp    0
dtype: int64

In [6]:
data = data.sample(25000)
data

UserId   ProductId  Rating   Timestamp
528904    A9GT2XQL1KB5S  B0012UK304     3.0  1383696000
896628   A15PD7QHXUA69P  B002NYB5B4     4.0  1275436800
178575   A344HD88CETZZB  B000B9N0N4     5.0  1298937600
583169    AGKD9DCQC19MQ  B0017T398S     4.0  1320537600
1314526  A25BOXYOGZ87PC  B004W2ORIS     5.0  1394236800
...                 ...         ...     ...         ...
416912   A163392KHH24BX  B000TIX8WU     5.0  1355529600
2009571   ADYZOSTF9LZLD  B00ISW92F6     2.0  1404086400
1457497  A1VVCT7P34M4JQ  B005WTYEYW     5.0  1371600000
559957    ADSFKIX44X8JV  B0015IW3PG     4.0  1354579200
1515553  A1VEE4EGL4CJPM  B006NKJSNQ     2.0  1358640000

[25000 rows x 4 columns]

In [7]:
data.shape

(25000, 4)

In [8]:
unique_users = data['UserId'].unique()
print(len(unique_users))

24430


In [9]:
unique_products = data['ProductId'].unique()
print(len(unique_products))

17525


In [10]:
new_df = pd.DataFrame(unique_users)
new_df.columns=['UserId']

In [11]:
for product in unique_products:
    new_df[product] = None

C:\Users\binur\AppData\Local\Temp\ipykernel_960\732139935.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  new_df[product] = None
C:\Users\binur\AppData\Local\Temp\ipykernel_960\732139935.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  new_df[product] = None
C:\Users\binur\AppData\Local\Temp\ipykernel_960\732139935.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis

In [12]:
for j,user in enumerate(new_df['UserId'].values):
    for i in range (data[data['UserId']==user].shape[0]):
        product_id = data[data['UserId']==user]['ProductId'].iloc[i]
        rating = data[data['UserId']==user]['Rating'].iloc[i]
        new_df[product_id][j] = rating

In [13]:
new_df.sample(5)

UserId B0012UK304 B002NYB5B4 B000B9N0N4 B0017T398S B004W2ORIS  \
16676   ALXGL9FNY7YDU       None       None       None       None       None   
102     A87Z7F5QLFAFF       None       None       None       None       None   
20853  A2DPQ2N7SG2CVG       None       None       None       None       None   
9388   A1LBMLNAM7G81E       None       None       None       None       None   
23786   AMCXM4RV54AFP       None       None       None       None       None   

      B00JCPKE28 B001D9ZK8E B009GETW5U B006QREEZS  ... B003VIQZE8 B0026P3HHK  \
16676       None       None       None       None  ...       None       None   
102         None       None       None       None  ...       None       None   
20853       None       None       None       None  ...       None       None   
9388        None       None       None       None  ...       None       None   
23786       None       None       None       None  ...       None       None   

      B006M9PGBG B003I9KMR6 B001TJ5RJA B0002YLW5Q B005NIT86G B00ISW92F6  \
16676       None       None       None       None       None       None   
102         None       None       None       None       None       None   
20853       None       None       None       None       None       None   
9388        None       None       None       None       None       None   
23786       None       None       None       None       None       None   

      B0015IW3PG B006NKJSNQ  
16676       None       None  
102         None       None  
20853       None       None  
9388        None       None  
23786       None       None  

[5 rows x 17526 columns]

In [15]:
user = pd.DataFrame(new_df.iloc[2142]) #randomly select user
user = user.drop(['UserId'])
user[user.notnull().values]

2142
B001HTCYPC  5.0

In [17]:
subset = new_df[new_df[user[user.notnull().values].index[0]].notnull()]
subset.head()

UserId B0012UK304 B002NYB5B4 B000B9N0N4 B0017T398S B004W2ORIS  \
806    A36YL7EZ51O6KZ       None       None       None       None       None   
2142   A1U5JF4DGJ72XK       None       None       None       None       None   
22744   AFD9JJ6RBG006       None       None       None       None       None   

      B00JCPKE28 B001D9ZK8E B009GETW5U B006QREEZS  ... B003VIQZE8 B0026P3HHK  \
806         None       None       None       None  ...       None       None   
2142        None       None       None       None  ...       None       None   
22744       None       None       None       None  ...       None       None   

      B006M9PGBG B003I9KMR6 B001TJ5RJA B0002YLW5Q B005NIT86G B00ISW92F6  \
806         None       None       None       None       None       None   
2142        None       None       None       None       None       None   
22744       None       None       None       None       None       None   

      B0015IW3PG B006NKJSNQ  
806         None       None  
2142        None       None  
22744       None       None  

[3 rows x 17526 columns]

In [19]:
subset = subset.replace([None],0)
subset = subset.set_index('UserId')

In [20]:
subset.head()

B0012UK304  B002NYB5B4  B000B9N0N4  B0017T398S  B004W2ORIS  \
UserId                                                                       
A36YL7EZ51O6KZ           0           0           0           0           0   
A1U5JF4DGJ72XK           0           0           0           0           0   
AFD9JJ6RBG006            0           0           0           0           0   

                B00JCPKE28  B001D9ZK8E  B009GETW5U  B006QREEZS  B001DKRM8O  \
UserId                                                                       
A36YL7EZ51O6KZ           0           0           0           0           0   
A1U5JF4DGJ72XK           0           0           0           0           0   
AFD9JJ6RBG006            0           0           0           0           0   

                ...  B003VIQZE8  B0026P3HHK  B006M9PGBG  B003I9KMR6  \
UserId          ...                                                   
A36YL7EZ51O6KZ  ...           0           0           0           0   
A1U5JF4DGJ72XK  ...           0           0           0           0   
AFD9JJ6RBG006   ...           0           0           0           0   

                B001TJ5RJA  B0002YLW5Q  B005NIT86G  B00ISW92F6  B0015IW3PG  \
UserId                                                                       
A36YL7EZ51O6KZ           0           0           0           0           0   
A1U5JF4DGJ72XK           0           0           0           0           0   
AFD9JJ6RBG006            0           0           0           0           0   

                B006NKJSNQ  
UserId                      
A36YL7EZ51O6KZ           0  
A1U5JF4DGJ72XK           0  
AFD9JJ6RBG006            0  

[3 rows x 17525 columns]

In [31]:
subset['cos_similarity'] = 0.0
for user in subset.index:
    cos = cosine_similarity(subset.loc['A36YL7EZ51O6KZ'].values.reshape(1,-1),subset.loc[user].values.reshape(1,-1))
    subset['cos_similarity'][user] = cos

C:\Users\binur\AppData\Local\Temp\ipykernel_960\3214666156.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subset['cos_similarity'][user] = cos
C:\Users\binur\AppData\Local\Temp\ipykernel_960\3214666156.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subset['cos_similarity'][user] = cos
C:\Users\binur\AppData\Local\Temp\ipykernel_960\3214666156.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subset['cos_similarity'][user] =

In [32]:
subset['cos_similarity']

UserId
A36YL7EZ51O6KZ    1.000000
A1U5JF4DGJ72XK    0.948683
AFD9JJ6RBG006     0.948683
Name: cos_similarity, dtype: float64